This notebook adds accumulated columns for fatigue factors rallies played, points played, and distance ran throughout a match. The output will only contain these columns as well as match identifiers and accumulated game numbers. This file takes a long time to run all. Instead run only relevant blocks if necessary.

In [1]:
# files involved and metric/factor availability
total_files = ["2011-usopen-points.csv","2011-ausopen-points.csv","2011-wimbledon-points.csv",
               "2011-frenchopen-points.csv","2012-usopen-points.csv","2012-ausopen-points.csv",
               "2012-wimbledon-points.csv","2012-frenchopen-points.csv","2013-usopen-points.csv",
               "2013-ausopen-points.csv","2013-wimbledon-points.csv","2013-frenchopen-points.csv",
               "2014-usopen-points.csv","2014-ausopen-points.csv","2014-wimbledon-points.csv",
               "2014-frenchopen-points.csv","2015-usopen-points.csv","2015-ausopen-points.csv",
               "2015-wimbledon-points.csv","2015-frenchopen-points.csv","2016-usopen-points.csv",
               "2016-ausopen-points.csv","2016-wimbledon-points.csv","2016-frenchopen-points.csv",
               "2017-usopen-points.csv","2017-ausopen-points.csv","2017-wimbledon-points.csv",
               "2017-frenchopen-points.csv","2018-usopen-points.csv","2018-ausopen-points.csv",
               "2018-wimbledon-points.csv","2018-frenchopen-points.csv","2019-usopen-points.csv",
               "2019-ausopen-points.csv","2019-wimbledon-points.csv","2019-frenchopen-points.csv",
               "2020-usopen-points.csv","2020-ausopen-points.csv","2021-wimbledon-points.csv",
               "2020-frenchopen-points.csv","2021-usopen-points.csv","2021-ausopen-points.csv",
               "2022-wimbledon-points.csv","2021-frenchopen-points.csv"]
# PointNumber/PointsAcc available in all files
rally_avail = ["2011-usopen-points.csv","2011-ausopen-points.csv","2011-wimbledon-points.csv",
               "2011-frenchopen-points.csv",]
# RallyCount / Rally are different fields in the datasets
rallycount_avail = ["2016-usopen-points.csv","2016-frenchopen-points.csv","2016-wimbledon-points.csv",
                    "2017-usopen-points.csv","2017-frenchopen-points.csv","2017-wimbledon-points.csv",
                    "2018-usopen-points.csv","2018-frenchopen-points.csv","2018-wimbledon-points.csv",
                    "2019-usopen-points.csv","2019-frenchopen-points.csv","2019-wimbledon-points.csv",
                    "2021-usopen-points.csv","2021-frenchopen-points.csv","2021-wimbledon-points.csv",
                    "2020-usopen-points.csv","2020-frenchopen-points.csv","2022-wimbledon-points.csv",
                    "2017-ausopen-points.csv","2018-ausopen-points.csv","2019-ausopen-points.csv",
                    "2020-ausopen-points.csv","2021-ausopen-points.csv"]
distance_avail = ["2015-usopen-points.csv","2015-frenchopen-points.csv","2015-wimbledon-points.csv",
                  "2016-usopen-points.csv","2016-frenchopen-points.csv","2016-wimbledon-points.csv",
                  "2017-usopen-points.csv","2017-frenchopen-points.csv","2017-wimbledon-points.csv",
                  "2016-ausopen-points.csv","2017-ausopen-points.csv","2018-wimbledon-points.csv",
                  "2019-wimbledon-points.csv","2021-wimbledon-points.csv","2022-wimbledon-points.csv",
                  "2018-usopen-points.csv","2019-usopen-points.csv","2020-usopen-points.csv",
                  "2021-usopen-points.csv"]

In [2]:
# fields to collect/calculate
r_fields = ["MatchID","ElapsedTime","GameNo","GameNoAcc","Rallies","RalliesAcc"]
p_fields = ["MatchID","ElapsedTime","GameNo","GameNoAcc","PointsAcc"]
d_fields = ["MatchID","ElapsedTime","GameNo","GameNoAcc","P1Distance","P1DistanceAcc","P2Distance","P2DistanceAcc"]
r_ret = "pbp_rallies.csv"
p_ret = "pbp_points.csv"
d_ret = "pbp_distance.csv"

In [3]:
import os
import csv

In [4]:
path = os.getcwd() # "...\\Code" parallel with "Data Lake"
path = path[:-4]+"Data Lake\\Point-By-Point\\" # all involved files use this same path
r_path = path+r_ret
p_path = path+p_ret
d_path = path+d_ret

In [10]:
def add_game_acc(points):
    """
    given list of points' information, where each point dict has field "GameNo",
    mutates list by adding field "GameNoAcc" which counts total games played for a match
    """
    prev_match = "invalid-match-id"
    prev_gameno = -1 # invalid GameNo value
    for point in points:
        if prev_match!=point["MatchID"]:
            gameno_acc = 0
            prev_match = point["MatchID"]
        if prev_gameno!=point["GameNo"]:
            # not checking for case where previous match retired at game 1
            gameno_acc += 1
            prev_gameno = point["GameNo"]
        point["GameNoAcc"] = gameno_acc
    return

def my_val(val,integer):
    """
    some of these entries will be missing, so if an empty string is encountered,
    want it just to be 0
    """
    try:
        if integer:
            return(int(val))
        else:
            return(float(val))
    except ValueError:
        return(0)

def add_acc_field(points,field,integer=True):
    """
    given list of points' information and field (which is the exact string),
    add the accumulation of that field's values for each match
    the added field will have name field+"Acc"
    invalid values in the field will be processed as 0 and at the end of a match,
    if the accumulated field value is still zero, this match's entries are discarded
    integer indicateds if the field contains integer values. If False, will have to 
    deal with floating point errors
    """
    
    matches_to_delete = []
    acc = 0
    prev_match = "invalid-match-id"
    # the 2 inits above will put "invalid-match-id" into the list
    # of matches to delete, but this is okay
    for point in points:
        if point["MatchID"]!=prev_match:
            # if this match's final acc value is still 0
            # delete all points pertaining to this match
            if acc == 0:
                matches_to_delete.append(prev_match)
            acc = 0
            prev_match = point["MatchID"]
        acc += my_val(point[field],integer=integer)
        point[field+"Acc"] = acc
    # now delete the matches empty with respect to field
    points_copy = points.copy() # shallow copy to iterate over
    
    for point in points_copy:
        if point["MatchID"] in matches_to_delete:
            print(point["MatchID"])
            points.remove(point)

## Rallies

In [11]:
r_points = [] # each item to be a dict containing info on a single point
# go through tournaments with [Rally] field available
for tournament in total_files:
    if tournament not in rally_avail:
        continue
    t_path = path+tournament
    with open(t_path,'r') as t:
        csvreader = csv.reader(t)
        fields = next(csvreader)
        match_id_idx = fields.index("match_id")
        time_idx = fields.index("ElapsedTime")
        game_idx = fields.index("GameNo")
        rally_idx = fields.index("Rally")
        for point in csvreader:
            # take relevant entries present
            r_point = {}
            r_point["MatchID"] = point[match_id_idx]
            r_point["ElapsedTime"] = point[time_idx]
            r_point["GameNo"] = point[game_idx]
            r_point["Rallies"] = point[rally_idx]
            r_points.append(r_point)
# go through tournaments with [RallyCount] field available
for tournament in total_files:
    if tournament not in rallycount_avail:
        continue
    t_path = path+tournament
    with open(t_path,'r') as t:
        csvreader = csv.reader(t)
        fields = next(csvreader)
        match_id_idx = fields.index("match_id")
        time_idx = fields.index("ElapsedTime")
        game_idx = fields.index("GameNo")
        rally_idx = fields.index("RallyCount")
        for point in csvreader:
            # take relevant entries present
            r_point = {}
            r_point["MatchID"] = point[match_id_idx]
            r_point["ElapsedTime"] = point[time_idx]
            r_point["GameNo"] = point[game_idx]
            r_point["Rallies"] = point[rally_idx]
            r_points.append(r_point)

In [12]:
# add accumulated fields
add_game_acc(r_points)
add_acc_field(r_points,"Rallies")

2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchopen-1116
2016-frenchop

2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchopen-1310
2016-frenchop

2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchopen-2311
2016-frenchop

2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchopen-1107
2017-frenchop

2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchopen-1114
2017-frenchop

...

2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2159
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161
2022-wimbledon-2161


2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203
2022-wimbledon-2203


2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211
2022-wimbledon-2211


2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219
2022-wimbledon-2219


2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227
2022-wimbledon-2227


In [13]:
with open(r_path,'w',newline="") as csvfile:
    writer = csv.DictWriter(csvfile, fieldnames=r_fields)
    writer.writeheader()
    writer.writerows(r_points)

## Points

In [14]:
p_points = []
for tournament in total_files:
    t_path = path+tournament
    with open(t_path,'r') as t:
        csvreader = csv.reader(t)
        fields = next(csvreader)
        match_id_idx = fields.index("match_id")
        time_idx = fields.index("ElapsedTime")
        game_idx = fields.index("GameNo")
        point_idx = fields.index("PointNumber")
        for point in csvreader:
            # take relevant entries present
            p_point = {}
            p_point["MatchID"] = point[match_id_idx]
            p_point["ElapsedTime"] = point[time_idx]
            p_point["GameNo"] = point[game_idx]
            p_point["PointsAcc"] = point[point_idx]
            p_points.append(p_point)
add_game_acc(p_points)
# since did not run through my_val, will contain entries like '0X','0Y',
# but shouldn't be a problem since values are cumulative

In [15]:
with open(p_path,'w',newline="") as csvfile:
    writer = csv.DictWriter(csvfile, fieldnames=p_fields)
    writer.writeheader()
    writer.writerows(p_points)

## Distance Ran

In [16]:
d_points = []
for tournament in total_files:
    if tournament not in distance_avail:
        continue
    t_path = path+tournament
    with open(t_path,'r') as t:
        csvreader = csv.reader(t)
        fields = next(csvreader)
        match_id_idx = fields.index("match_id")
        time_idx = fields.index("ElapsedTime")
        game_idx = fields.index("GameNo")
        p1d_idx = fields.index("P1DistanceRun")
        p2d_idx = fields.index("P2DistanceRun")
        for point in csvreader:
            # take relevant entries present
            d_point = {}
            d_point["MatchID"] = point[match_id_idx]
            d_point["ElapsedTime"] = point[time_idx]
            d_point["GameNo"] = point[game_idx]
            d_point["P1Distance"] = point[p1d_idx]
            d_point["P2Distance"] = point[p2d_idx]
            d_points.append(d_point)

In [17]:
# add accumulated fields
add_game_acc(d_points)
# commenting out 2 lines below as the length of their output prevents
# printing to pdf
add_acc_field(d_points,"P1Distance",integer=False)
add_acc_field(d_points,"P2Distance",integer=False)

2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-1108
2015-usopen-11

2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-1141
2015-usopen-11

2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-1154
2015-usopen-11

2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-1204
2015-usopen-12

2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-1215
2015-usopen-12

...

2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2230
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-2231
2020-usopen-22

2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1223
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227
2022-wimbledon-1227


2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229
2022-wimbledon-1229


2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-1230
2022-wimbledon-2202
2022-wimbledon-2202
2022-wimbledon-2202
2022-wimbledon-2202
2022-wimbledon-2202
2022-wimbledon-2202
2022-wimbledon-2202
2022-wimbledon-2202


2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209
2022-wimbledon-2209


In [18]:
with open(d_path,'w',newline="") as csvfile:
    writer = csv.DictWriter(csvfile, fieldnames=d_fields)
    writer.writeheader()
    writer.writerows(d_points)

In [19]:
len(d_points)

520151

In [45]:
# starting length is 774111
# second time over 1 hour down to 538695
# final cut down to 520151